# mm include

Dieses Notebook:
* lese eine Freeplane-Mindmap ein
* für Text-Knoten, die mit "°i " beginnen: lies die danach angegebene Mindmap ein

## Beispiel

* Input: die Mindmap {download}`test.mm`
* Output: die JSON-Datei {download}`test-included.mm`

In [22]:
mm_path = "test.mm"

In [2]:
# wir verwenden die xml und xslt-Engine
# https://lxml.de/
from lxml import etree

In [7]:
def open_mm(mm_path):
    parser = etree.XMLParser(remove_blank_text=True)
    etree_tree = etree.parse(mm_path, parser)
    etree_startnode = etree_tree.getroot().find("node")
    return etree_tree, etree_startnode

In [20]:
def walk(current, included):
    """Returns a nested dict representation of a freeplane mindmap."""    
    
    [ current.attrib.pop(a, None) for a in ['HGAP_QUANTITY', 'VSHIFT_QUANTITY'] ]

    # Liste aller "node"-Kinder des aktuellen Knotens
    # (andere XML-Elemente sind uninteressant)
    children = current.findall("node[@TEXT]")
    
    if len(children) >= 1:
        # der aktuelle Knoten *hat* Kinder:
        for child in children:
            text = child.get("TEXT")
            if text.startswith("°i "):
                to_include_file_path = text.split()[1]
                if to_include_file_path not in included:
                    _, include_root = open_mm(to_include_file_path)
                    included.append(to_include_file_path)
                    print(f"included {to_include_file_path}: {include_root.get('TEXT')}")
                    child.append(include_root)
                else:
                    print(f"WARNING: rejecting multiple inclusion of {to_include_file_path}")
                    
            walk(child, included)

In [24]:
import os

In [28]:
workdir = "."
os.chdir(workdir)
mm_path = "test.mm"
etree_tree, etree_startnode = open_mm(mm_path)

In [27]:
included = [ mm_path ]
walk( etree_startnode, included)
included


included test2.mm, node, Root von test2


['test.mm', 'test2.mm']

Wir schreiben das Ergebnis wieder 'raus:

In [19]:
etree_tree.write(f"{mm_path}_included.mm", pretty_print=True)